# import libraries

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import re

import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

from sklearn.naive_bayes import (BernoulliNB, ComplementNB, MultinomialNB,)
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neural_network import MLPClassifier
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC

In [2]:
# read data
data_df = pd.read_csv('scrap_naukri_jobs.csv')
data_df.head()

Designation  \
0  Assistant Team Lead, Drupal Frontend Developer   
1      Lead/Senior UI Frontend Developer - Vue.js   
2            Lead/Senior UI or Frontend Developer   
3       React.js Developer (Frontend) - Bangalore   
4                             FRONTEND  DEVELOPER   

                          Company Name                         Salary  \
0                Cvent3.6(246 Reviews)                  Not Disclosed   
1       Squareroot Consulting Pvt Ltd.                  Not Disclosed   
2       Squareroot Consulting Pvt Ltd.                  Not Disclosed   
3  K12 Techno Services3.2(357 Reviews)  ₹ 10,00,000 - 18,00,000 P.A.    
4                        Serving Skill                  Not Disclosed   

    Experience                        Location  \
0  4 - 6 years  Gurgaon/Gurugram( Cyber City )   
1  3 - 8 years             Bangalore/Bengaluru   
2  3 - 8 years             Bangalore/Bengaluru   
3  3 - 8 years             Bangalore/Bengaluru   
4  4 - 8 years             Bangalore/Bengaluru   

                                 Role  \
0  IT & Information Security - Other,   
1                Front End Developer,   
2                Front End Developer,   
3                Front End Developer,   
4                Front End Developer,   

                                              Skills  \
0        Twig,CSS,Javascript,Drupal 8,Bootstrap,HTML   
1  Angularjs,CSS,Artificial Intelligence,Redux,HT...   
2  CSS,Scalable,HTML,JSON,Vue.Js,Front End,UI,JQu...   
3  Redux,Flux,Javascript,React.js,Wireframing,JSO...   
4  CSS,JavaScript,HTML,Front End,Vue,Bootstrap,JS...   

                                       Qualification          Industry Type  \
0                               ['UG :Any Graduate']      Software Product,   
1  ['UG :B.Tech/B.E. in Any Specialization', 'PG ...              Internet,   
2  ['UG :B.Tech/B.E. in Any Specialization, BCA i...              Internet,   
3                   ['UG :B.Tech/B.E. in Computers']  Education / Training,   
4  ['UG :B.Tech/B.E. in Any Specialization', 'PG ...              Internet,   

                Functional Area       Employment Type  \
0    IT & Information Security,  Full Time, Permanent   
1  Engineering - Software & QA,  Full Time, Permanent   
2  Engineering - Software & QA,  Full Time, Permanent   
3  Engineering - Software & QA,  Full Time, Permanent   
4  Engineering - Software & QA,  Full Time, Permanent   

                       Role Category  \
0  IT & Information Security - Other   
1               Software Development   
2               Software Development   
3               Software Development   
4               Software Development   

                                             Address  \
0  AddressBuilding No. 14,Unit 1 - 19th Floor Tow...   
1             Websitehttp://jobs.squarerootindia.com   
2             Websitehttp://jobs.squarerootindia.com   
3  AddressNo 60/1 1st Main Road, \nIndustrial Sub...   
4                                           Address.   

                                             Post By    Post Date  \
0  DeekshaSenior Technical Recruiter at Cvent Ind...   2 days ago   
1  Pawan WalvekarAsociate Manager Recruitment at ...    1 day ago   
2  Pawan WalvekarAsociate Manager Recruitment at ...    1 day ago   
3                                                NaN    1 day ago   
4                                                NaN    1 day ago   

                                             Website  \
0  https://www.naukri.com/cvent-jobs-careers-1400...   
1  https://www.naukri.com/squareroot-consulting-j...   
2  https://www.naukri.com/squareroot-consulting-j...   
3  https://www.naukri.com/k12-techno-services-job...   
4  https://www.naukri.com/premium-jobs-careers-85...   

                                                 Url  \
0  https://www.naukri.com/cvent-jobs-careers-1400...   
1  https://www.naukri.com/squareroot-consulting-j...   
2  https://www.naukri.com/squareroot-consulting-j...   
3  https://www.naukri.c

In [3]:
# # remove Address, Post Date, Post By, Website, Url
data_df.drop(['Address', 'Website', 'Url','About Company','Post Date','Post By', 'Employment Type','Location'], inplace=True, axis=1)
data_df.head()

Designation  \
0  Assistant Team Lead, Drupal Frontend Developer   
1      Lead/Senior UI Frontend Developer - Vue.js   
2            Lead/Senior UI or Frontend Developer   
3       React.js Developer (Frontend) - Bangalore   
4                             FRONTEND  DEVELOPER   

                          Company Name                         Salary  \
0                Cvent3.6(246 Reviews)                  Not Disclosed   
1       Squareroot Consulting Pvt Ltd.                  Not Disclosed   
2       Squareroot Consulting Pvt Ltd.                  Not Disclosed   
3  K12 Techno Services3.2(357 Reviews)  ₹ 10,00,000 - 18,00,000 P.A.    
4                        Serving Skill                  Not Disclosed   

    Experience                                Role  \
0  4 - 6 years  IT & Information Security - Other,   
1  3 - 8 years                Front End Developer,   
2  3 - 8 years                Front End Developer,   
3  3 - 8 years                Front End Developer,   
4  4 - 8 years                Front End Developer,   

                                              Skills  \
0        Twig,CSS,Javascript,Drupal 8,Bootstrap,HTML   
1  Angularjs,CSS,Artificial Intelligence,Redux,HT...   
2  CSS,Scalable,HTML,JSON,Vue.Js,Front End,UI,JQu...   
3  Redux,Flux,Javascript,React.js,Wireframing,JSO...   
4  CSS,JavaScript,HTML,Front End,Vue,Bootstrap,JS...   

                                       Qualification          Industry Type  \
0                               ['UG :Any Graduate']      Software Product,   
1  ['UG :B.Tech/B.E. in Any Specialization', 'PG ...              Internet,   
2  ['UG :B.Tech/B.E. in Any Specialization, BCA i...              Internet,   
3                   ['UG :B.Tech/B.E. in Computers']  Education / Training,   
4  ['UG :B.Tech/B.E. in Any Specialization', 'PG ...              Internet,   

                Functional Area                      Role Category  \
0    IT & Information Security,  IT & Information Security - Other   
1  Engineering - Software & QA,               Software Development   
2  Engineering - Software & QA,               Software Development   
3  Engineering - Software & QA,               Software Development   
4  Engineering - Software & QA,               Software Development   

                                     Job Description  
0  Job descriptionCvent is looking for an Assista...  
1  Job descriptionRoles and Responsibilities Our ...  
2  Job descriptionRoles and Responsibilities Our ...  
3  Job descriptionOrganization Brief:K12 Techno S...  
4  Job descriptionExp: 4-7 years(SDE-2)Skills: Ve...

In [4]:
data_df.columns

Index(['Designation', 'Company Name', 'Salary', 'Experience', 'Role', 'Skills',
       'Qualification', 'Industry Type', 'Functional Area', 'Role Category',
       'Job Description'],
      dtype='object')

In [5]:
# preprocess all data
list_processed_data = []

for row in data_df.itertuples(name='Pandas', index=False):
    inner_ = []
    for i in row:
        print(i)
        i = re.sub(r'\W', ' ', str(i))
#         i = i.lower()
        i = re.sub(r'\s+[a-zA-Z]\s+', ' ', i)
        i = re.sub(r'\s+', ' ', i, flags=re.I)
        inner_.append(i)
    list_processed_data.append(inner_)

Assistant Team Lead, Drupal Frontend Developer
Cvent3.6(246 Reviews)
Not Disclosed
4 - 6 years
IT & Information Security - Other,
Twig,CSS,Javascript,Drupal 8,Bootstrap,HTML
['UG :Any Graduate']
Software Product,
IT & Information Security,
IT & Information Security - Other
Job descriptionCvent is looking for an Assistant Team Lead to join the growing Web Marketing team. The candidate will report directly to the Sr. Manager, Web Marketing and be responsible for strategizing, managing, and executing various web development efforts for Cvents global websites.What you will be doing: Developing custom, responsive web pages and static HTML prototypes using design comps and style guides Evaluating wireframes and user flows to ensure they follow established design guidelines and stakeholder requirements before converting them into HTML Optimizing web pages for maximum speed and scalability Building reusable code for future use Writing semantic, standards-compliant HTML and CSS Collaborating wi

Not Disclosed
3 - 8 years
Software Development - Other,
React Native
['UG :Any Graduate']
Software Product,
Engineering - Software & QA,
Software Development
Job description Roles and Responsibilities  Understandthebusinesscontextandbuildhighqualitycodeusingprovendesignandarchitectural      patternsDevelop, test and deploy integrations required to meet business requirements.Carryoutunittestsandotherqualitycontrolmechanismstoinformandvalidatethecodeand      design.Utilizing and monitoring cloud infrastructure resources (such as AWS, Azure)      efficiently.Participateinahighpacedandfluidenvironmentapplyingagilesoftwaredevelopmentprinciples      with immediate business impact.Ensure      the coding standards are on-par with the best in the industry.Desired Candidate Profile Bachelor's or Mastersdegree in a quantitative field (e.g.Mathematics,Engineering,Computer Science).         Good problem solving skillsStrong knowledge of CS fundamentals, data structures.Experience in working with fr

Software Development
Job description   Job Qualifications      Education:     Bachelor s Degree in Information Technology, MIS, or related field.     Backend Developer     Minimum of 9 years of experience in the software industry   Experience acting as a team lead for developers, including supervisory responsibilities   Compile and analyze data, processes, and codes to troubleshoot problems and identify areas for improvement.   Collaborating with the frontend developers and other team members to establish objectives and design functional, cohesive code   Strong understanding of ObjectOriented Design (OOD) principles   Experience in designing Rich UI web applications and web service applications using UI technologies [Object oriented javaScript]   Knowledge in developing applications using ava, SpringBoot, Spring Webservices, Spring Security applications using JSON and REST services   Knowledge in configuring cloud platform, Active directory, web security, webapps and web tokens   Exper

['UG :Any Graduate']
Software Product,
Engineering - Software & QA,
Software Development
Job descriptionWe are hiring for Front End Developer position for Pune location with Upgrad Rekrut for one of the leading companies.Job details:Exp - 3 to 8 years	CTC - As per marketLocation - Pune (Hybrid work mode)Roles and Responsibilities:Should have expertise in web development using Angular 8.Should have experience of working in fully agile teams with solutions deployed to cloud.Should use tools such as GitLab, Jira, Confluence and DockerShould have used Unit Test Frameworks like JunitShould have used Javascript / Typescript / HTMLKnowledge of Observables / RxJs and reactive design patternsShould have good with / SASS / SCSSIf you are Interested then kindly share you resume on given email id: akshay.r@ipsgroup.co.inRoleFront End Developer,Industry TypeSoftware Product,Functional AreaEngineering - Software & QA,Employment TypeFull Time, PermanentRole CategorySoftware DevelopmentEducationUG :An

Java,Ruby Rails,Spring Boot,AWS,Microservices,Ux Design,Javascript,Cicd Pipeline,React.Js,Python
['UG :B.Tech/B.E. in Any Specialization']
Software Product,
Project & Program Management,
Technology / IT
Job descriptionMission and Scope For Cloud and Digital team, seek Hands-On Technical Lead who can work on designing & implementing high quality scalable cloud software while providing technical leadership/mentoring to a small team of developers in agile environmentRequired Candidate profileExperience in Web and Mobile software development and coding in various languages (Ruby on Rails, Node.js, Java, React, Python etc.). Familiarity with HTML/CSS, JavaScript and UI/UX designRoleProgram Manager - Technology / IT,Industry TypeSoftware Product,Functional AreaProject & Program Management,Employment TypeFull Time, PermanentRole CategoryTechnology / ITEducationUG :B.Tech/B.E. in Any SpecializationKey SkillsJavaRuby RailsSpring BootAWSMicroservicesUx DesignJavascriptCicd PipelineReact.JsPython

...

['UG :BCA in Any Specialization, B.Sc in Any Specialization, B.Tech/B.E. in Any Specialization']
Pharmaceutical & Life Sciences,
Engineering - Software & QA,
Software Development
Job description Dear Candidate,Greetings from LexisNexis Risk SolutionsWe are hiring for Software Developer (Bigdata) role with LexisNexis Risk Solutions for Mumbai and Chennai location QUALIFICATIONS:   3+ years of Software Engineering experience   BS Engineering/Computer Science or equivalent experience required.   Early joining candidates preferred.TECHNICAL SKILLS:Strong analytical skills, Communication, Problem Solving skills.Strong Knowledge on SQL.Knowledge on software development lifecycle.Good understanding on Data Manipulation Language, basic ETL concepts .Basic knowledge on any of the language  Python, Java script, any ETL tool.Must have real time project exp and also have better understanding of the ETL  Data processing, Facts and Dimension, Data Profiling, knowledge in using any ETL tool  Talend, 

5 - 10 years
Back End Developer,
Mobile application development,GIT,Mobile development,html5,Analytical,Agile development,Debugging,Javascript,android studio,CSS3
['UG :Any Graduate', 'PG :Post Graduation Not Required']
Recruitment / Staffing,
Engineering - Software & QA,
Software Development
Job description        Have hands-on experience in mobile application  development for iOS and Android platforms utilizing React Native.   Have experienced with cross-platform mobile development using HTML5,  CSS3, JavaScript, NodeJs, ReactJs and related technologies.  Thrive  in fast-paced and agile development environments.  Proficient with  React Native, Redux, and TypesScript Familiar in Objective-C or  Java Experience using common design patterns.  High standards for  code quality, maintainability, and performance.  Good analytical  debugging skills.  Familiarity with code versioning tools such as  Git.  Understanding of REST APIs, offline storage, and ability to  integrate third party APIs. 

Full Stack Developer,
Software Engineering,Java,CSS,Hibernate,UX,HTML,NodeJS,UI,ReactJS,MySQL,Javascript,Bootstrap,MongoDB,Springboot
['UG :B.Tech/B.E. in Any Specialization', 'PG :Any Postgraduate', 'Doctorate :Doctorate Not Required']
Internet,
Engineering - Software & QA,
Software Development
Job descriptionKey Responsibilities/ Position Details:Plan, organize and develop user-facing features for the components in our dynamic ads platform.Write and optimize client-side code of the web applications, create fast application with good UI/UXWork with other members to develop and integrate new features including other third-party systems and plugins into our platform.Evaluate and identify new technologies for implementation and incorporation.Communicate with our business and product heads to understand clients’ requirements.Respond and follow up to incorporate feedback and draw new insights.Prioritize tasks to meet multiple deadlines.Requirements. At least 2-4 years of working experience

Android SDK,Java,Retrofit,Git,RxJava,Eclipse,CI/CD,Dagger,Android Studio
['UG :B.Tech/B.E. in Any Specialization', 'PG :MCA in Any Specialization']
Medical Services / Hospital,
Engineering - Software & QA,
Software Development
Job descriptionRequirements   Essential -Academic Qualification: B.E/B.Tech, MCA with consistent academic   performance from X, XII standards onwards. Experience: Minimum 5 Years. Strong critical thinking, problem solving, analytical, and design skills  Excellent verbal and written communication skills Thorough understanding of   OOP concepts  Knowledge of Android SDK, Native development  advanced level   Hands-on experience on Clean architecture, RxJava, Retrofit, Dagger   Injection, Android architecture components Hands-on experience in building   Business applications in Android SDK Stack, Android Studio or Eclipse as IDE, Java SDK, Git, CI/CD.RoleMobile / App Developer,Industry TypeMedical Services / Hospital,Functional AreaEngineering - Software & QA,Employm

Job description Greetings from ThunderSoft India Private Limited !!ThunderSoft is the world's Leading Intelligent Platform Technology Provider. Head Quartered in Beijing, China, we have a presence in more than 20 cities across the globe. We service more than 1000 customers and have 600+ patents to our name.ThunderSoft Hyderabad is currently hiring for Graphic Driver Developer , please find the below details.Experience:- 1 to 6 Years  Position:- Graphic Driver DeveloperC/C++ programming skillsOpenGL/Vulkan driver development experienceLinux/Android and/or Windows development experiencePreferred to have:Knowledge of and/or experience with Shader Compiler is a plusD3D/Vulkan/OpenGL (ES) graphics application knowledge and experience is a plusRoleSoftware Development - Other,Industry TypeSoftware Product,Functional AreaEngineering - Software & QA,Employment TypeFull Time, PermanentRole CategorySoftware DevelopmentEducationUG :Any GraduateKey SkillsGraphics DriverLinux GraphicLi nuxopengl es

In [6]:
list_processed_data[3]

['React js Developer Frontend Bangalore',
 'K12 Techno Services3 2 357 Reviews ',
 ' 10 00 000 18 00 000 A ',
 '3 8 years',
 'Front End Developer ',
 'Redux Flux Javascript React js Wireframing JSON Rest API Webpack Code Versioning Tools',
 ' UG Tech E in Computers ',
 'Education Training ',
 'Engineering Software QA ',
 'Software Development',
 'Job descriptionOrganization Brief K12 Techno Services Pvt Ltd was incorporated in the year 2010 and with its registered office in Bangalore is leading education service provider in India offering dynamic suite of academic support services and solutions to schools The upgraded teaching methodologies blended with effective use of technology has been the main idea behind the organization e to pave the way for global approach towards education With its band of services facilitate schools to leverage on its strength Planning academics and its execution with teachers and resource management are some of the key features of our academic support and se

In [7]:
processed_ = pd.DataFrame(list_processed_data, columns=data_df.columns)

In [8]:
processed_

Designation  \
0         Assistant Team Lead Drupal Frontend Developer   
1              Lead Senior UI Frontend Developer Vue js   
2                  Lead Senior UI or Frontend Developer   
3                 React js Developer Frontend Bangalore   
4                                    FRONTEND DEVELOPER   
...                                                 ...   
1919                   Senior Product Software Engineer   
1920      Senior Software Engineer Net Fullstack Azure    
1921  Senior Staff Embedded Software Engineer Matter...   
1922                               Sr Engineer Software   
1923                                    Full Stack Lead   

                                   Company Name                   Salary  \
0                         Cvent3 6 246 Reviews             Not Disclosed   
1                Squareroot Consulting Pvt Ltd             Not Disclosed   
2                Squareroot Consulting Pvt Ltd             Not Disclosed   
3           K12 Techno Services3 2 357 Reviews    10 00 000 18 00 000 A    
4                                 Serving Skill            Not Disclosed   
...                                         ...                      ...   
1919             Wolters Kluwer3 9 208 Reviews             Not Disclosed   
1920             Wolters Kluwer3 9 208 Reviews             Not Disclosed   
1921             ESPRESSIF SYSTEMS SHANGHAI PTE            Not Disclosed   
1922     ICE Mortgage Technology4 4 47 Reviews             Not Disclosed   
1923  VEHERE INTERECTIVE PVT LTD4 0 20 Reviews             Not Disclosed   

       Experience                            Role  \
0       4 6 years  IT Information Security Other    
1       3 8 years            Front End Developer    
2       3 8 years            Front End Developer    
3       3 8 years            Front End Developer    
4       4 8 years            Front End Developer    
...           ...                             ...   
1919    4 8 years             Back End Developer    
1920   5 10 years     Software Development Other    
1921   5 15 years             Back End Developer    
1922   8 13 years             Back End Developer    
1923  10 15 years             Back End Developer    

                                                 Skills  \
0           Twig CSS Javascript Drupal 8 Bootstrap HTML   
1     Angularjs CSS Artificial Intelligence Redux HT...   
2     CSS Scalable HTML JSON Vue Js Front End UI JQu...   
3     Redux Flux Javascript React js Wireframing JSO...   
4     CSS JavaScript HTML Front End Vue Bootstrap JS...   
...                                                 ...   
1919  Performance tuning jQuery Coding Web developme...   
1920  IIS Javascript Agile Scrum Application securit...   
1921  Unix RTOS Wireless Bluetooth Semiconductor Lin...   
1922  Computer science Object oriented design System...   
1923  Restful Apis Front End Typescript Html5 Javasc...   

                                          Qualification  \
0                                      UG Any Graduate    
1      UG Tech E in Any Specialization PG Tech in An...   
2      UG Tech E in Any Specialization BCA in Any Sp...   
3                               UG Tech E in Computers    
4      UG Tech E in Any Specialization PG MCA in Any...   
...                                                 ...   
1919               UG Any Graduate PG Any Postgraduate    
1920               UG Any Graduate PG Any Postgraduate    
1921               UG Any Graduate PG Any Postgraduate    
1922   UG Any Graduate PG Post Graduation Not Required    
1923               UG Any Graduate PG Any Postgraduate    

                              Industry Type           Functional Area  \
0                         Software Product   IT Information Security    
1                                 Internet   Engineering Software QA    
2                                 Internet   Engineering Software QA    
3                       Education Training   Engineering Software QA    
4 

In [9]:
# # create description, experience, title and other column
replace_ = ['Company Name', 'Location', 'Role','Qualification','Industry Type','Functional Area','Salary'
          'Employment Type','Role Category', 'Address','Post By', 'Post Date', 'Website','Url','About Company']
# data_df['others'] = data_df[columns].to_dict(orient='records')


In [10]:
test_df = pd.DataFrame([(i, j) for a in processed_.to_dict('records') for i, j in a.items()], 
                   columns=['labels', 'data'])

print(test_df)

                labels                                               data
0          Designation      Assistant Team Lead Drupal Frontend Developer
1         Company Name                              Cvent3 6 246 Reviews 
2               Salary                                      Not Disclosed
3           Experience                                          4 6 years
4                 Role                     IT Information Security Other 
...                ...                                                ...
21159    Qualification               UG Any Graduate PG Any Postgraduate 
21160    Industry Type                                       Telecom ISP 
21161  Functional Area                           Engineering Software QA 
21162    Role Category                               Software Development
21163  Job Description  Job description You will be part of the team t...

[21164 rows x 2 columns]


In [11]:
test_df['labels'] = test_df['labels'].replace(replace_,'others')

In [12]:
test_df

labels                                               data
0          Designation      Assistant Team Lead Drupal Frontend Developer
1               others                              Cvent3 6 246 Reviews 
2               Salary                                      Not Disclosed
3           Experience                                          4 6 years
4               others                     IT Information Security Other 
...                ...                                                ...
21159           others               UG Any Graduate PG Any Postgraduate 
21160           others                                       Telecom ISP 
21161           others                           Engineering Software QA 
21162           others                               Software Development
21163  Job Description  Job description You will be part of the team t...

[21164 rows x 2 columns]

In [13]:
test_df['labels'].value_counts()

others             11544
Designation         1924
Salary              1924
Experience          1924
Skills              1924
Job Description     1924
Name: labels, dtype: int64

In [14]:
from sklearn import preprocessing

le = preprocessing.LabelEncoder()
test_df['labels'] = le.fit_transform(test_df.labels.values)

In [15]:
test_df.head(10)

labels                                           data
0       0  Assistant Team Lead Drupal Frontend Developer
1       5                          Cvent3 6 246 Reviews 
2       3                                  Not Disclosed
3       1                                      4 6 years
4       5                 IT Information Security Other 
5       4    Twig CSS Javascript Drupal 8 Bootstrap HTML
6       5                               UG Any Graduate 
7       5                              Software Product 
8       5                       IT Information Security 
9       5                  IT Information Security Other

In [16]:
le.classes_

array(['Designation', 'Experience', 'Job Description', 'Salary', 'Skills',
       'others'], dtype=object)

In [17]:
le.inverse_transform([5])

array(['others'], dtype=object)

In [18]:
data = test_df.data.values

In [19]:
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

vectorizer = TfidfVectorizer(max_features=2500, min_df=7, max_df=0.8, stop_words=stopwords.words('english'))
# vectorizer = CountVectorizer()
processed_features = vectorizer.fit_transform(data).toarray()

In [20]:
len(processed_features[0])

2500

In [21]:
processed_features.shape

(21164, 2500)

In [22]:
labels = test_df['labels']
labels

0        0
1        5
2        3
3        1
4        5
        ..
21159    5
21160    5
21161    5
21162    5
21163    2
Name: labels, Length: 21164, dtype: int64

In [23]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(processed_features, labels, test_size=0.2, random_state=0)

In [24]:
print(len(X_train))
print(len(X_test))
print(len(y_train))
print(len(y_test))

16931
4233
16931
4233


In [25]:
len(X_train[0])

2500

In [26]:
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score


def get_accuracy(model, x_train, y_train, x_test, y_test):
    if model == 'RandomForestClassifier':
        text_classifier = model(n_estimators=200, random_state=0)
    elif model =='KNeighborsClassifier':
        text_classifier = model(n_neighbors=9, leaf_size=20)
    else:
        text_classifier = model()
        
    text_classifier.fit(x_train, y_train)

    predictions = text_classifier.predict(x_test)
    print("Classifier: ", model)
    
    print("Confusion matrix: \n",confusion_matrix(y_test,predictions))
    print("classification report: \n",classification_report(y_test,predictions))
    print("accuracy score:\n",accuracy_score(y_test, predictions))
    print("---------------------------------------------------------------")
    input_ = ['7-8 years','Java,Python,Machine learning','Python Developer', 'Mumbai,Maharashtra','Talend developer']
    new_testdata_tfidf= vectorizer.transform(input_)


    #transform the new data to see if the feature remove or not, because after tfidf i use chi2 selection feature.
    predicted = text_classifier.predict(new_testdata_tfidf)
    
    print("data: ", input_)
    print("predicted field ",le.inverse_transform(predicted))
    

    print("#######################################")


## Random Forest classifier

In [28]:
get_accuracy(RandomForestClassifier, X_train, y_train, X_test, y_test)



Classifier:  <class 'sklearn.ensemble._forest.RandomForestClassifier'>
Confusion matrix: 
 [[ 373    0    0    0    6   17]
 [   0  359    0    0    0    0]
 [   0    0  376    0    0    0]
 [   0    0    0  363    0    0]
 [   9    0    0    0  375    9]
 [   2    0    0    0    0 2344]]
classification report: 
               precision    recall  f1-score   support

           0       0.97      0.94      0.96       396
           1       1.00      1.00      1.00       359
           2       1.00      1.00      1.00       376
           3       1.00      1.00      1.00       363
           4       0.98      0.95      0.97       393
           5       0.99      1.00      0.99      2346

    accuracy                           0.99      4233
   macro avg       0.99      0.98      0.99      4233
weighted avg       0.99      0.99      0.99      4233

accuracy score:
 0.9898417198204583
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Machine 

## Logistic Regression 

In [29]:
get_accuracy(LogisticRegression, X_train, y_train, X_test, y_test)

Classifier:  <class 'sklearn.linear_model._logistic.LogisticRegression'>
Confusion matrix: 
 [[ 352    0    0    0    3   41]
 [   0  358    0    0    0    1]
 [   0    0  374    0    0    2]
 [   0    0    0  363    0    0]
 [   3    0    0    0  369   21]
 [   5    0    0    0    2 2339]]
classification report: 
               precision    recall  f1-score   support

           0       0.98      0.89      0.93       396
           1       1.00      1.00      1.00       359
           2       1.00      0.99      1.00       376
           3       1.00      1.00      1.00       363
           4       0.99      0.94      0.96       393
           5       0.97      1.00      0.98      2346

    accuracy                           0.98      4233
   macro avg       0.99      0.97      0.98      4233
weighted avg       0.98      0.98      0.98      4233

accuracy score:
 0.9815733522324592
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Machin

## AdaBoostClassifier 

In [30]:
get_accuracy(AdaBoostClassifier, X_train, y_train, X_test, y_test)


Classifier:  <class 'sklearn.ensemble._weight_boosting.AdaBoostClassifier'>
Confusion matrix: 
 [[   0    0    0    0    0  396]
 [ 359    0    0    0    0    0]
 [   0    0  375    0    0    1]
 [   0    0    0    0    0  363]
 [   0    0    0    0    0  393]
 [   0    0    0    0    0 2346]]
classification report: 
               precision    recall  f1-score   support

           0       0.00      0.00      0.00       396
           1       0.00      0.00      0.00       359
           2       1.00      1.00      1.00       376
           3       0.00      0.00      0.00       363
           4       0.00      0.00      0.00       393
           5       0.67      1.00      0.80      2346

    accuracy                           0.64      4233
   macro avg       0.28      0.33      0.30      4233
weighted avg       0.46      0.64      0.53      4233

accuracy score:
 0.6428065201984409
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Mac

/home/neosoft/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/neosoft/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/neosoft/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


## BernoulliNB 

In [31]:
get_accuracy(BernoulliNB, X_train, y_train, X_test, y_test)


Classifier:  <class 'sklearn.naive_bayes.BernoulliNB'>
Confusion matrix: 
 [[ 345    0    0    2    3   46]
 [   0  359    0    0    0    0]
 [   0    0  376    0    0    0]
 [   0    0    0  363    0    0]
 [  22    0    0    4  355   12]
 [  47    0    0    2    2 2295]]
classification report: 
               precision    recall  f1-score   support

           0       0.83      0.87      0.85       396
           1       1.00      1.00      1.00       359
           2       1.00      1.00      1.00       376
           3       0.98      1.00      0.99       363
           4       0.99      0.90      0.94       393
           5       0.98      0.98      0.98      2346

    accuracy                           0.97      4233
   macro avg       0.96      0.96      0.96      4233
weighted avg       0.97      0.97      0.97      4233

accuracy score:
 0.9669265296480037
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Machine learning', 'Pyth

# MultinomialNB

In [32]:
get_accuracy(MultinomialNB, X_train, y_train, X_test, y_test)


Classifier:  <class 'sklearn.naive_bayes.MultinomialNB'>
Confusion matrix: 
 [[ 322    0    1    0   14   59]
 [   0  358    0    1    0    0]
 [   0    0  376    0    0    0]
 [   0    0    0  363    0    0]
 [  12    0    1    0  369   11]
 [   7    0    3    0    5 2331]]
classification report: 
               precision    recall  f1-score   support

           0       0.94      0.81      0.87       396
           1       1.00      1.00      1.00       359
           2       0.99      1.00      0.99       376
           3       1.00      1.00      1.00       363
           4       0.95      0.94      0.94       393
           5       0.97      0.99      0.98      2346

    accuracy                           0.97      4233
   macro avg       0.98      0.96      0.97      4233
weighted avg       0.97      0.97      0.97      4233

accuracy score:
 0.9730687455705174
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Machine learning', 'Py

#  ComplementNB

In [33]:
get_accuracy(ComplementNB, X_train, y_train, X_test, y_test)

Classifier:  <class 'sklearn.naive_bayes.ComplementNB'>
Confusion matrix: 
 [[ 308    1   19    0   32   36]
 [   0  359    0    0    0    0]
 [   0    0  376    0    0    0]
 [   0    0    0  363    0    0]
 [   9    0   16    0  359    9]
 [  66    0   18    0   13 2249]]
classification report: 
               precision    recall  f1-score   support

           0       0.80      0.78      0.79       396
           1       1.00      1.00      1.00       359
           2       0.88      1.00      0.93       376
           3       1.00      1.00      1.00       363
           4       0.89      0.91      0.90       393
           5       0.98      0.96      0.97      2346

    accuracy                           0.95      4233
   macro avg       0.92      0.94      0.93      4233
weighted avg       0.95      0.95      0.95      4233

accuracy score:
 0.9482636428065202
---------------------------------------------------------------
data:  ['7-8 years', 'Java,Python,Machine learning', 'Pyt